In [5]:
!pip install selenium
!pip install webdriver-manager
!pip install pandas


Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 30.2 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 346.6/346.6 KB 23.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 32.2 MB/s eta 0:00:0000:0100:01


In [7]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager
import pandas as pd
import time
import re
import os

try:
    driver = webdriver.Chrome()
except:
    print("AF: No Chrome webdriver installed")
    driver = webdriver.Chrome(ChromeDriverManager().install())

try:
    url = "https://www.forexfactory.com/calendar?month=jan.2008"
    driver.get(url)
    while True:
        before_scroll = driver.execute_script("return window.pageYOffset;")
        driver.execute_script("window.scrollTo(0, window.pageYOffset + 500);")
        time.sleep(2)
        after_scroll = driver.execute_script("return window.pageYOffset;")
        if before_scroll == after_scroll:
            break

    # Get the table
    table = driver.find_element(By.CLASS_NAME, "calendar__table")
    data = []
    last_date = None
    last_time = None
    currency_codes = ['CAD', 'JPY', 'USD', 'GBP', 'EUR', 'NZD', 'AUD', 'CHF', 'CNY']

    for row in table.find_elements(By.TAG_NAME, "tr"):
        row_data = []
        for td in row.find_elements(By.TAG_NAME, "td"):
            if td.text:
                text = td.text.replace('\n', ', ')
                row_data.append(text)
                if ',' in text:  
                    last_date = text
                elif re.match(r'\d+:\d+[ap]m', text):
                    last_time = text
            else:
                if td.get_attribute("class") == "calendar__cell calendar__impact":
                    span_element = td.find_element(By.TAG_NAME, 'span')
                    row_data.append(span_element.get_attribute("title"))
        row_data = [x for x in row_data if x is not None] 
        if row_data and len(row_data) > 1:  
            if row_data[0] == 'Tentative':  
                row_data.insert(0, last_time)  
                row_data.insert(0, last_date)  
            elif row_data[0].startswith('Day'):  
                row_data.insert(0, last_date)  
            elif row_data[0] in currency_codes:  
                row_data.insert(0, last_time)  
                row_data.insert(0, last_date)  
            elif row_data[0] == 'All Day' or re.match(r'\d+:\d+[ap]m', row_data[0]):  
                row_data.insert(0, last_date)  
            data.append(row_data)
            print(row_data)

    second_list = ['CAD', 'JPY', 'USD', 'GBP', 'EUR', 'NZD', 'AUD', 'CHF', 'CNY']
    result_list = [[None] + row if len(row) > 1 and row[1] in second_list else row for row in data]
    result_list = [[None] + [None] + row if len(row) > 0 and row[0] in second_list else row for row in result_list]

    # Ensure each row has 8 elements
    for i in range(len(result_list)):
        while len(result_list[i]) < 8:
            result_list[i].append('')

    column_names = ['Date', 'Time', 'Currency', 'Impact', 'Event', 'Actual', 'Forecast', 'Previous']
    df = pd.DataFrame(result_list)
    df.columns = column_names

    month_year = url.split('=')[-1]
    year = month_year.split('.')[-1]

    directory = f'data/{year}'
    if not os.path.exists(directory):
        os.makedirs(directory)

    df.to_csv(f'{directory}/{month_year}.csv', index=False)
    print("done")

except Exception as e:
    print(e)

finally:
    driver.quit()

['Tue, Jan 1', 'All Day', 'CHF', 'Non-Economic', 'Bank Holiday']
['Tue, Jan 1', 'All Day', 'EUR', 'Non-Economic', 'German Bank Holiday']
['Tue, Jan 1', 'All Day', 'EUR', 'Non-Economic', 'French Bank Holiday']
['Tue, Jan 1', 'All Day', 'EUR', 'Non-Economic', 'Italian Bank Holiday']
['Tue, Jan 1', 'All Day', 'GBP', 'Non-Economic', 'Bank Holiday']
['Tue, Jan 1', 'All Day', 'CAD', 'Non-Economic', 'Bank Holiday']
['Tue, Jan 1', 'All Day', 'USD', 'Non-Economic', 'Bank Holiday']
['Tue, Jan 1', 'All Day', 'NZD', 'Non-Economic', 'Bank Holiday']
['Tue, Jan 1', '5:30pm', 'AUD', 'Low Impact Expected', 'AIG Manufacturing Index', '57.6', '53.8']
['Tue, Jan 1', 'All Day', 'CNY', 'Non-Economic', 'Bank Holiday']
['Tue, Jan 1', 'All Day', 'JPY', 'Non-Economic', 'Bank Holiday']
['Tue, Jan 1', '9:30pm', 'CNY', 'Medium Impact Expected', 'Caixin Manufacturing PMI', '53.3', '52.8']
['Wed, Jan 2', '12:30am', 'AUD', 'Medium Impact Expected', 'Commodity Prices y/y', '1.8%', '1.6%']
['Wed, Jan 2', 'All Day', 'CH

In [17]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time
import re
import os

def setup_driver():
    try:
        return webdriver.Chrome()
    except:
        print("AF: No Chrome webdriver installed")
        return webdriver.Chrome(ChromeDriverManager().install())

months = ['jan', 'feb', 'mar', 'apr', 'may', 'jun', 'jul', 'aug', 'sep', 'oct', 'nov', 'dec']
years = range(2007, 2025)  # 2025 is exclusive, so it will stop at 2024

def set_zoom(driver, zoom):
    driver.execute_script(f"document.body.style.zoom='{zoom}%'")

driver = setup_driver()  # Initial setup

try:
    for year in years:
        for month in months:
            url = f"https://www.forexfactory.com/calendar?month={month}.{year}"
            driver.get(url)

            # Set zoom to 80%
            set_zoom(driver, 90)
            driver.maximize_window()

            while True:
                before_scroll = driver.execute_script("return window.pageYOffset;")
                driver.execute_script("window.scrollTo(0, window.pageYOffset + 500);")
                time.sleep(2)
                after_scroll = driver.execute_script("return window.pageYOffset;")
                if before_scroll == after_scroll:
                    break

            wait = WebDriverWait(driver, 60)
            table = wait.until(EC.presence_of_element_located((By.CLASS_NAME, "calendar__table")))

            data = []
            last_date = None
            last_time = None
            currency_codes = ['CAD', 'JPY', 'USD', 'GBP', 'EUR', 'NZD', 'AUD', 'CHF', 'CNY']

            for row in table.find_elements(By.TAG_NAME, "tr"):
                row_data = []
                for td in row.find_elements(By.TAG_NAME, "td"):
                    if td.text:
                        text = td.text.replace('\n', ', ')
                        row_data.append(text)
                        if ',' in text:  
                            last_date = text
                        elif re.match(r'\d+:\d+[ap]m', text):
                            last_time = text
                    else:
                        if td.get_attribute("class") == "calendar__cell calendar__impact":
                            span_element = td.find_element(By.TAG_NAME, 'span')
                            row_data.append(span_element.get_attribute("title"))
                row_data = [x for x in row_data if x is not None] 
                if row_data and len(row_data) > 1:  
                    if row_data[0] == 'Tentative':  
                        row_data.insert(0, last_time)  
                        row_data.insert(0, last_date)  
                    elif row_data[0].startswith('Day'):  
                        row_data.insert(0, last_date)  
                    elif row_data[0] in currency_codes:  
                        row_data.insert(0, last_time)  
                        row_data.insert(0, last_date)  
                    elif row_data[0] == 'All Day' or re.match(r'\d+:\d+[ap]m', row_data[0]):  
                        row_data.insert(0, last_date)  
                    data.append(row_data)
                    print(row_data)

            second_list = ['CAD', 'JPY', 'USD', 'GBP', 'EUR', 'NZD', 'AUD', 'CHF', 'CNY']
            result_list = [[None] + row if len(row) > 1 and row[1] in second_list else row for row in data]
            result_list = [[None] + [None] + row if len(row) > 0 and row[0] in second_list else row for row in result_list]

            # Ensure each row has 8 elements
            for i in range(len(result_list)):
                while len(result_list[i]) < 8:
                    result_list[i].append('')

            column_names = ['Date', 'Time', 'Currency', 'Impact', 'Event', 'Actual', 'Forecast', 'Previous']
            df = pd.DataFrame(result_list)
            df.columns = column_names

            directory = f'data/{year}'
            if not os.path.exists(directory):
                os.makedirs(directory)

            df.to_csv(f'{directory}/{month}.{year}.csv', index=False)
            print(f"Data for {month} {year} saved.")

            driver.quit()  # Close the browser after processing each month
            if not (year == years[-1] and month == months[-1]):  # Avoid setting up a new driver after the last iteration
                driver = setup_driver()  # Setup a new driver for the next iteration

except Exception as e:
    print(e)

finally:
    driver.quit()


['Wed, Jan 3', 'Low Impact Expected']
['Wed, Jan 3', 'All Day', 'USD', 'Low Impact Expected', 'Total Vehicle Sales', '16.7M', '16.5M', '16.1M']
['Wed, Jan 3', '2:00pm', 'USD', 'High Impact Expected', 'FOMC Meeting Minutes']
['Wed, Jan 3', '4:45pm', 'NZD', 'High Impact Expected', 'Trade Balance', '-785M', '-976M', '-1174M']
['Wed, Jan 3', '5:30pm', 'AUD', 'Low Impact Expected', 'AIG Services Index', '49.5', '48.5']
['Thu, Jan 4', '1:45am', 'CHF', 'High Impact Expected', 'CPI m/m', '0.0%', '0.1%', '0.0%']
['Thu, Jan 4', '3:15am', 'EUR', 'Low Impact Expected', 'Spanish Services PMI', '58.1', '60.4']
['Thu, Jan 4', '3:45am', 'EUR', 'Low Impact Expected', 'Italian Services PMI', '55.0', '56.2', '56.2']
['Thu, Jan 4', '4:00am', 'EUR', 'Low Impact Expected', 'Final Services PMI', '57.2', '57.5', '57.6']
['Thu, Jan 4', '4:30am', 'GBP', 'Medium Impact Expected', 'Final Services PMI', '60.6', '60.0', '59.8']
['Thu, Jan 4', '4:30am', 'GBP', 'Low Impact Expected', 'Mortgage Approvals', '129K', '12